In [2]:
import pandas as pd
import numpy as np
from pythainlp import word_tokenize
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn.metrics import classification_report, confusion_matrix
# import joblib
# import seaborn as sns
import matplotlib.pyplot as plt
from imblearn.over_sampling import SMOTE
import json
import glob

from pythainlp.corpus import thai_stopwords

In [5]:
file_pattern = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/TripAdvisor_reviews_TH.csv')

In [ ]:
file_pattern

In [8]:
file_pattern = '../dataset/reviews/TripAdvisor_reviews_TH_Set-*.json'
files = glob.glob(file_pattern)

# Step 2: Initialize an empty list to store the combined data
combined_reviews_data = []

# Step 3: Load each file and concatenate the contents
for file in files:
    with open(file, 'r') as f:
        data = json.load(f)
        combined_reviews_data.extend(data)

In [10]:
combined_reviews_data

[{'2209612': [{'id': 922231809,
    'lang': 'th',
    'location_id': 2209612,
    'published_date': '2023-10-21T01:18:50Z',
    'rating': 5,
    'helpful_votes': 0,
    'rating_image_url': 'https://www.tripadvisor.com/img/cdsi/img2/ratings/traveler/s5.0-66827-5.svg',
    'url': 'https://www.tripadvisor.com/ShowUserReviews-g293916-d2209612-r922231809-Reviews-Wat_Ratchabophit-Bangkok.html?m=66827#review922231809',
    'text': 'เป็นวัดที่สร้างขึ้นในรัชกาลที่ 5 \nพระบาทสมเด็จพระจุลจอมเกล้าเจ้าอยู่หัว\nมีสถาปัตยกรรมไทยผสมกับกอธิก\nมีพระประธานนามว่า พระพุทธอังคีรส\nมีสร้อยนามว่า สถิตมหาสีมาราม',
    'title': 'วัดราชบพิตร สถิตมหาสีมาราม',
    'trip_type': 'ครอบครัว',
    'travel_date': '2023-10-31',
    'user': {'username': 'maxzerk',
     'user_location': {'id': '293916', 'name': 'Bangkok'},
     'avatar': {'thumbnail': 'https://media-cdn.tripadvisor.com/media/photo-t/2a/a2/f5/e4/caption.jpg',
      'small': 'https://media-cdn.tripadvisor.com/media/photo-l/2a/a2/f5/e4/caption.jpg',
      'me

In [11]:
len(combined_reviews_data)

1521

In [14]:
tripadvisor_central_attraction_locations = pd.read_csv("../dataset/locations/TripAdvisor_Location_Ids.csv")
tripadvisor_central_attraction_locations

Unnamed: 0  location_id  \
0              0      2209612   
1              1      2273363   
2              2       311043   
3              3       317504   
4              4       456322   
...          ...          ...   
1899        6905     13009981   
1900        6906      3256228   
1901        6907      2515972   
1902        6911     13365103   
1903        6912      2645868   

                                                 name         province  \
0                                    Wat Ratchabophit          Bangkok   
1     Wat Rajapradit Sathitmahasimaram Rajaworavihara          Bangkok   
2                                  Wat Phra Chetuphon          Bangkok   
3                           Temple Of Dawn (Wat Arun)          Bangkok   
4                                           Wat Umong          Bangkok   
...                                               ...              ...   
1899                               Thai Sabai Massage  Samut Songkhram   
1900                          Phuket Dragon Muay Thai  Samut Songkhram   
1901                       Thai Cooking School Phuket  Samut Songkhram   
1902                     Nong Bua Thai Dessert Market  Samut Songkhram   
1903                     Free Thai (Seri Thai) Museum  Samut Songkhram   

       place_id  
0     P03013220  
1     P03013220  
2     P03013220  
3     P03013220  
4     P03013220  
...         ...  
1899  P03012297  
1900  P03012297  
1901  P03012297  
1902  P03000251  
1903  P03000251  

[1904 rows x 5 columns]

In [ ]:
normalize_reviews_data = pd.DataFrame()

for location_data in combined_reviews_data:
    for location_id, reviews in location_data.items():
        print(f"Location ID: {location_id}")

        # Iterate over each review in the list of reviews
        for review in reviews:
            # Create a DataFrame for each review
            review_df = pd.DataFrame([{
                "helpful_votes": review.get("helpful_votes", 0),
                "location_id": review.get("location_id", None),
                "lang": review.get("lang", None),
                "review_id": review.get("id", None),
                "review": review.get("text", None),
                "review_subject": review.get("title", None),
                "trip_type": review.get("trip_type", None),
                "travel_date": review.get("travel_date", None),
                "rating": review.get("rating", 0)
            }])

            # Concatenate the current review DataFrame with the normalized DataFrame
            normalize_reviews_data = pd.concat([normalize_reviews_data, review_df], ignore_index=True)

normalize_reviews_data.replace("None", None, inplace=True)

In [16]:
normalize_reviews_data

helpful_votes  location_id lang  review_id  \
0                 0      2209612   th  922231809   
1                18      2209612   th  777982512   
2                 0      2209612   th  738367222   
3                 2      2209612   th  737450116   
4                 0      2209612   th  690288478   
...             ...          ...  ...        ...   
6081              0      2645868   th  495275277   
6082              0      2645868   th  437755007   
6083              0      2645868   th  361116911   
6084              0      2645868   th  332354742   
6085              0      2645868   th  245695590   

                                                 review  \
0     เป็นวัดที่สร้างขึ้นในรัชกาลที่ 5 \nพระบาทสมเด็...   
1     ตั้งอยู่ด้านทิศตะวันตกของวัด มีประตูเข้าตรงทาง...   
2     วันนี้เป็นที่พำนักของพระสังฆราชองค์ใหม่ ตอนไปก...   
3     วันนี้เป็นบุญของครอบครัวเราแท้ๆมีโอกาส ได้เข้า...   
4     พอดีมาแถว ถ.เฟื่องนครเลยได้แวะมาวัดนี้ ตอนกลาง...   
...                                                 ...   
6081  เป็นอาคารเชิงประวัติศาสตร์ ตั้งอยู่หลังโรงแรมภ...   
6082  เป็นสถานที่ที่รวบรวมข้อมูล เอกสาร สิ่งของ ต่าง...   
6083  สถานที่รวบรมประวัติการดำเนินงานของผู้กล้าที่ทำ...   
6084  การมาท่องเที่ยวที่นี่ เราจะได้เรียนรู้ถึงเรื่อ...   
6085  ปกติตรงนั้นจะมีโรงแรมภรดร ครับถือโอกาสใกล้ที่พ...   

                     review_subject         trip_type travel_date  rating  
0        วัดราชบพิตร สถิตมหาสีมาราม          ครอบครัว  2023-10-31       5  
1                       ชมสุสานหลวง  เดินทางกับเพื่อน  2020-11-30       5  
2                           ไหว้พระ            คู่รัก  2019-12-31       5  
3      กราบสักการะ สมเด็จพระสังฆราช              NONE  2019-12-31       5  
4                        วัดราชบพิธ          ครอบครัว  2019-07-31       4  
...                             ...               ...         ...     ...  
6081             บ้านเสรีไทย จ.แพร่    เดินทางคนเดียว  2017-06-30       5  
6082                 รวบรวมของโบราณ            คู่รัก  2016-11-30       3  
6083              ระลึกถึงความดีงาม              NONE  2016-03-31       5  
6084  พิพิธภัณฑ์เสรีไทย จังหวัดแพร่    เดินทางคนเดียว  2015-11-30       4  
6085                 พักที่เดียวกัน          ครอบครัว  2014-11-30       3  

[6086 rows x 9 columns]

In [17]:
merged_df = normalize_reviews_data.merge(tripadvisor_central_attraction_locations[['location_id', 'name', 'province', 'place_id']], on='location_id', how='left')

# Rename the 'name' column to 'location_name'
merged_df.rename(columns={'name': 'location_name'}, inplace=True)
len(merged_df)

6086

In [24]:
merged_df.to_csv("../dataset/TripAdvisor_reviews_TH.csv")
# EN_tripadvisor_reviews = pd.read_csv("dataset/TripAdvisor_reviews_EN.csv")

In [18]:
# Define Thai stop words
thai_stopwords = thai_stopwords()

# Function to normalize text
def normalize_text(text):
    tokens = word_tokenize(text, engine='newmm')
    tokens = [token for token in tokens if token not in thai_stopwords and token.isalpha()]
    return ' '.join(tokens)

In [19]:
thai_stopwords

frozenset({'ทุกที่',
           'รับ',
           'ยืนนาน',
           'ช่วงหลัง',
           'มอง',
           'โดย',
           'ที่ว่า',
           'นับจากนั้น',
           'ประการฉะนี้',
           'แล้วแต่',
           'ยังจะ',
           'ตลอดทั่ว',
           'เขียน',
           'เป็นแต่',
           'ทีไร',
           'สิ่งไหน',
           'ถึงเมื่อไร',
           'สมัยโน้น',
           'เช่นก่อน',
           'แต่อย่างใด',
           'เพียงแต่',
           'คล้ายกับว่า',
           'จัดทำ',
           'ถึงอย่างไร',
           'ได้',
           'แห่งไหน',
           'นู่น',
           'คล้าย',
           'มัน',
           'จนกว่า',
           'เหล่านี้',
           'ครั้งไหน',
           'วันนั้น',
           'เช่นที่ว่า',
           'เนี่ยเอง',
           'นับจากนี้',
           'เกี่ยวกัน',
           'ณ',
           'จัด',
           'ถึงแม้จะ',
           'แต่เพียง',
           'ประสบ',
           'ต่าง',
           'มา',
           'พวกเธอ',
           'ยืนยง',
           '

In [22]:
from pythainlp import word_tokenize
from pythainlp.util import normalize
from string import punctuation

In [23]:
def preprocess_thai_text(text):
    # Normalize the text (e.g., harmonizing character representations)
    text = normalize(text)

    # Lowercasing (Thai text does not differentiate case, but we include for consistency)
    text = text.lower()

    # Removing punctuation
    thai_punctuation = punctuation + 'ๆฯ'  # Extend punctuation to include common Thai characters
    text = text.translate(str.maketrans('', '', thai_punctuation))

    # Tokenization (Thai-specific tokenization)
    tokens = word_tokenize(text, engine='newmm')  # 'newmm' is a recommended tokenizer

    # # Removing stopwords
    # thai_stopwords = set(stopwords.words('thai'))
    tokens = [word for word in tokens if word not in thai_stopwords]

    # Removing non-Thai characters (optional, if mixed-language input)
    tokens = [word for word in tokens if all('\u0E00' <= char <= '\u0E7F' for char in word)]

    # Return the preprocessed text as a string of tokens
    return ' '.join(tokens)